These are screens are those that I follow from: *What Works on Wall Street, Fourth Edition: The Classic Guide to the Best-Performing Investment Strategies of All Time.* 

This is just my interpretation of the books material.

**This material is not intended to be relied upon as a forecast, research or investment advice, and is not a recommendation. Past performance is not always indicative of future returns. I may or may not own stocks listed**

# R System Prep

Data was downloaded the day that I run this notebook. Data should be 1 market day old.

This sheet was run on: 

In [1]:
Sys.time()

[1] "2022-08-01 11:46:36 PDT"

First initialize R environment:

In [2]:
suppressPackageStartupMessages(library(tidyverse))
suppressPackageStartupMessages(library(tidyquant))
suppressPackageStartupMessages(library(rio))
suppressPackageStartupMessages(library(knitr))
suppressPackageStartupMessages(library(kableExtra))
suppressPackageStartupMessages(library(IRdisplay))
#library(kableExtra)

<!-- TEASER_END -->
Read Data

In [3]:
#setwd("D:/OneDrive/SITES/www.michaelghens.com/Rdocs")
universe <-
  read.csv(
    "STOCKS.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

universe_names <-
  read.csv(
    "STOCKS_KEY.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

names(universe) <- universe_names[, 2]
count1 <- nrow(universe)[1]

Fields imported:

In [4]:
universe_names[, 2] %>%
  kbl("html") %>%
  as.character() %>%
  display_html()

x 
 
 
 
 
 Ticker 
 
 
 Company name 
 
 
 Price Change 52 week 
 
 
 Yield 
 
 
 Sector 
 
 
 Industry 
 
 
 Exchange 
 
 
 ADR/ADS Stock 
 
 
 Market Cap Q1 
 
 
 Price Change 13 week 
 
 
 Price Change 26 week 
 
 
 Cash flow/share 12m 
 
 
 Shares Average Q1 
 
 
 Sales 12m 
 
 
 Buyback Yield 
 
 
 Price/Book 
 
 
 PE 
 
 
 Price/Sales 
 
 
 Enterprise Value/EBITDA 
 
 
 Price/CFPS 
 
 
 Shareholder Yield 
 
 
 1yr chg debt 
 
 
 External Financing 
 
 
 LT Debt/equity Q1 
 
 
 LT debt/free cash flow 12m 
 
 
 EarningsQuality

Fields:

* EarningsQuality: ([Cash from operations 12m]-[Net income 12m])/[Market Cap Q1]
* 1yr chg debt: [Long-term debt Q1]-[Long-term debt Q5])/[Long-term debt Q5]
* External Financing: [Cash from financing Q1]/[Total assets Q1]

Are caculated fields


To clean up the universe of stocks, they must:

* have a ticker
* market cap
* ~~13,26,52 week price change~~
* not be over the counter
* ~~not an ADR stock~~
* ~~not be a reit stock.~~
* ~~not be a closed end fund (TBA)~~

In [5]:
universe <- universe[complete.cases(universe$Ticker),]
universe <- universe[complete.cases(universe$`Market Cap Q1`),]
#universe <- universe[complete.cases(universe$`Price Change 13 week`),]
#universe <- universe[complete.cases(universe$`Price Change 26 week`),]
#universe <- universe[complete.cases(universe$`Price Change 52 week`),]
#exchanges
condition <- c("N - New York", "A - American", "M - Nasdaq")
universe <- filter(universe, Exchange %in% condition)
#universe <- filter(universe,`ADR/ADS Stock` == 'FALSE')
#universe <- filter(universe,!grepl('REITs',Industry))
count2 <- nrow(universe)[1]

# Market Cap Variables

Screens need some market cap and momentom constants

* Minimum deflated Market Cap all cap universe
* Mediam 13 and 26 Momentom for bear trap
* Average Market cap for large cap universe

Calculating deflator, mins, means and medians.

In [6]:
options("getSymbols.warning4.0"=FALSE)
#find inflation Market Cap 150 @ 1995
getSymbols("CPIAUCSL", src = "FRED", auto.assign=getOption('getSymbols.auto.assign',TRUE))
deflator  <-
  last(Cl(to.yearly(CPIAUCSL)))[[1]] / Cl(to.yearly(CPIAUCSL))['1995'][[1]]
mincap <- 150 * deflator
median13w <- median(universe$`Price Change 13 week`,  na.rm = TRUE)
median26w <- median(universe$`Price Change 26 week`,  na.rm = TRUE)
avgmcap <- mean(universe$`Market Cap Q1`,  na.rm = TRUE)
avgshares <- mean(universe$`Shares Average Q1`,  na.rm = TRUE)
avgcashflowshares <- mean(universe$`Cash flow/share 12m`,  na.rm = TRUE)
avgsales15 <- mean(universe$`Sales 12m`,  na.rm = TRUE) * 1.5

[1] "CPIAUCSL"

# Create stock unverses

Screens are based on thre inverses of stocks 

* smallstocks
* allstocks
* largestocks
* marketleaders

## Create means and medians 

In [7]:
smallstocks <- filter(universe, `Market Cap Q1` <= avgmcap & `Market Cap Q1` >= mincap)

allstocks <- filter(universe, `Market Cap Q1` >= mincap)

largestocks <- filter(universe, `Market Cap Q1` >= avgmcap)

marketleaders <- allstocks %>% filter(Sector != "59  - Utilities") %>% 
  filter(`Shares Average Q1` > avgshares) %>%
  filter(`Cash flow/share 12m` > avgcashflowshares) %>%
  filter(`Sales 12m` > avgsales15)

Function to add rankings

In [8]:
calcvc2 <- function(x) {
  #Calculate VC2
  #subtract ntile from 101 to reverse (correct) Order. So Small is big
  x$`Price/Book.Rank` <-
    100 - round(percent_rank(x$`Price/Book`) * 100, 1)
  x$PE.Rank <- 100 - round(percent_rank(x$PE) * 100, 1)
  x$`Price/Sales.Rank` <-
    100 - round(percent_rank(x$`Price/Sales`) * 100, 1)
  x$`Enterprise Value/EBITDA.Rank` <-
    100 - round(percent_rank(x$`Enterprise Value/EBITDA`) * 100, 1)
  x$`Price/CFPS.Rank` <-
    100 - round(percent_rank(x$`Price/CFPS`) * 100, 1)
  x$`Shareholder Yield.Rank` <-
    round(percent_rank(x$`Shareholder Yield`) * 100, 1)
  
  #Stocks with no rank get 50
  x$`Price/Book.Rank`[is.na(x$`Price/Book.Rank`)] <- 50
  x$PE.Rank[is.na(x$PE.Rank)] <- 50
  x$`Price/Sales.Rank`[is.na(x$`Price/Sales.Rank`)] <- 50
  x$`Enterprise Value/EBITDA.Rank`[is.na(x$`Enterprise Value/EBITDA.Rank`)] <-
    50
  x$`Price/CFPS.Rank`[is.na(x$`Price/CFPS.Rank`)] <- 50
  x$`Shareholder Yield.Rank`[is.na(x$`Shareholder Yield.Rank`)] <- 50
  #Sum the Ranks
  x$SumRank <-
    x$`Price/Book.Rank` + x$PE.Rank + x$`Price/Sales.Rank` + x$`Enterprise Value/EBITDA.Rank` + x$`Price/CFPS.Rank` + x$`Shareholder Yield.Rank`
  x$VC2 <- round(percent_rank(x$SumRank) * 100, 1)
  return(x)
}

allstocks <- calcvc2(allstocks)
largestocks <- calcvc2(largestocks)
marketleaders <- calcvc2(marketleaders)

## Market Cap discriptive

In [9]:
summary(select_if(allstocks,is.numeric))

 Price Change 52 week     Yield        Market Cap Q1       Price Change 13 week
 Min.   :-94.52       Min.   : 0.000   Min.   :    287.9   Min.   :-84.400     
 1st Qu.:-33.94       1st Qu.: 0.000   1st Qu.:    659.5   1st Qu.:-13.035     
 Median :-10.52       Median : 0.000   Median :   1936.4   Median : -1.800     
 Mean   :-10.96       Mean   : 1.513   Mean   :  13989.6   Mean   : -2.610     
 3rd Qu.:  4.97       3rd Qu.: 2.200   3rd Qu.:   6838.9   3rd Qu.:  5.125     
 Max.   :424.85       Max.   :44.900   Max.   :2537675.0   Max.   :392.050     
 NA's   :213                                               NA's   :11          
 Price Change 26 week Cash flow/share 12m Shares Average Q1  
 Min.   :-87.570      Min.   :-181.0900   Min.   :    0.452  
 1st Qu.:-17.800      1st Qu.:  -1.0300   1st Qu.:   39.902  
 Median : -3.730      Median :  -0.0200   Median :   81.250  
 Mean   : -2.579      Mean   :   0.3502   Mean   :  276.675  
 3rd Qu.:  7.225      3rd Qu.:   0.6100   3rd Qu.:

In [10]:
summary(largestocks$`Market Cap Q1`)

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
   8980   14914   26322   58619   51320 2537675 

In [11]:
summary(marketleaders$`Market Cap Q1`)

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
   2692   24175   46469   81451   97384  861140 

# Portfolios

## Trending Value

In [12]:
TrendingValue <- allstocks %>%  filter(VC2 >= 90) %>% arrange(desc(`Price Change 26 week`)) %>% slice_head(n = 25) %>% select(Ticker, `Company name`,Sector,Industry)

TrendingValue %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 PBF 
 PBF Energy Inc 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 CVLG 
 Covenant Logistics Group Inc 
 52 - Industrials 
 52405030 - Freight & Logistics - Ground 
 
 
 RFP 
 Resolute Forest Products Inc 
 51 - Basic Materials 
 51301020 - Paper Products 
 
 
 DSX 
 Diana Shipping Inc 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 LPG 
 Dorian LPG Ltd 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 BTE 
 Baytex Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 MERC 
 Mercer International Inc. 
 51 - Basic Materials 
 51301020 - Paper Products 
 
 
 STLD 
 Steel Dynamics, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 ZEUS 
 Olympic Steel, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 TMST 
 Timkensteel Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 NUE 
 Nucor Corporation 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 EQNR 
 Equinor ASA (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 UFCS 
 United Fire Group, Inc. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 VLO 
 Valero Energy Corporation 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 CVE 
 Cenovus Energy Inc (US) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 TGS 
 Transportadora de Gas del Sur 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 WIRE 
 Encore Wire Corporation 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 KELYA 
 Kelly Services, Inc. 
 52 - Industrials 
 52203030 - Employment Services 
 
 
 SANM 
 Sanmina Corp 
 57 - Technology 
 57101010 - Semiconductors 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 X 
 United States Steel Corporatio 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 PRDO 
 Perdoceo Education Corp 
 63 - Academic & Educational Services 
 63101010 - Miscellaneous Educational Service Providers 
 
 
 UNM 
 Unum Group 
 55 - Financials 
 55301030 - Insurance - Life & Health

## Cheap Stocks on the mend

In [13]:
cheapmend <-
  allstocks %>%  filter(VC2 >= 70) %>% filter(`Price Change 13 week` > median13w) %>% filter(`Price Change 26 week` >
                                        median26w) %>% arrange(desc(`Price Change 26 week`)) %>%             
                                        slice_head(n = 25) %>% select(Ticker, `Company name`)

cheapmend %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 
 
 
 
 CEIX 
 Consol Energy Inc 
 
 
 TEDU 
 Tarena International Inc(ADR) 
 
 
 ASC 
 Ardmore Shipping Corp 
 
 
 HMLP 
 Hoegh LNG Partners LP 
 
 
 AR 
 Antero Resources Corp 
 
 
 TAL 
 TAL Education Group (ADR) 
 
 
 PBF 
 PBF Energy Inc 
 
 
 VHI 
 Valhi, Inc. 
 
 
 ULH 
 Universal Logistics Holdings I 
 
 
 ARIS 
 Aris Water Solutions Inc 
 
 
 DQ 
 Daqo New Energy Corp (ADR) 
 
 
 OXY 
 Occidental Petroleum Corporati 
 
 
 SD 
 SandRidge Energy Inc. 
 
 
 CVI 
 CVR Energy, Inc. 
 
 
 DK 
 Delek US Holdings Inc 
 
 
 VET 
 Vermilion Energy Inc 
 
 
 BMEA 
 Biomea Fusion Inc 
 
 
 CVLG 
 Covenant Logistics Group Inc 
 
 
 MTOR 
 Meritor Inc 
 
 
 RFP 
 Resolute Forest Products Inc 
 
 
 AAV 
 Advantage Energy Ltd 
 
 
 DSX 
 Diana Shipping Inc 
 
 
 LPG 
 Dorian LPG Ltd 
 
 
 BTE 
 Baytex Energy Corp 
 
 
 QURE 
 Uniqure NV

## Market Leaders

### Price Appreciation

In [14]:
mlsy <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlsy %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 PBR 
 Petroleo Brasileiro SA Petrobr 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 BP 
 BP plc (ADR) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 SHEL 
 Shell PLC (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 ENB 
 Enbridge Inc (USA) 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 NXPI 
 NXP Semiconductors NV 
 57 - Technology 
 57101010 - Semiconductors 
 
 
 EQNR 
 Equinor ASA (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 CF 
 CF Industries Holdings, Inc. 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 GS 
 Goldman Sachs Group Inc 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 CVE 
 Cenovus Energy Inc (US) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 ADP 
 Automatic Data Processing Inc 
 57 - Technology 
 57201010 - IT Services & Consulting 
 
 
 NTES 
 NetEase Inc (ADR) 
 57 - Technology 
 57201030 - Online Services 
 
 
 EMR 
 Emerson Electric Co. 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 WM 
 Waste Management, Inc. 
 52 - Industrials 
 52203010 - Environmental Services & Equipment 
 
 
 COP 
 ConocoPhillips 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 FIS 
 Fidelity National Information 
 57 - Technology 
 57301010 - Fintech 
 
 
 OVV 
 Ovintiv Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 XOM 
 Exxon Mobil Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 UPS 
 United Parcel Service, Inc. 
 52 - Industrials 
 52405010 - Freight & Logistics - Courier, Postal, Air Freight & L 
 
 
 FISV 
 Fiserv Inc 
 52 - Industrials 
 52203040 - Business Support Services

In [15]:
mlvc2 <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(VC2)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlvc2 %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 PBR 
 Petroleo Brasileiro SA Petrobr 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 SHEL 
 Shell PLC (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 BP 
 BP plc (ADR) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 EQNR 
 Equinor ASA (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 CVE 
 Cenovus Energy Inc (US) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 BNTX 
 BioNTech SE - ADR 
 56 - Healthcare 
 56202010 - Biotechnology & Medical Research 
 
 
 GS 
 Goldman Sachs Group Inc 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 PPC 
 Pilgrim's Pride Corporation 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 CF 
 CF Industries Holdings, Inc. 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 ET 
 Energy Transfer LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 COP 
 ConocoPhillips 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 CEA 
 China Eastern Airlines Corp. L 
 52 - Industrials 
 52406010 - Airlines 
 
 
 CNC 
 Centene Corp 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 PSX 
 Phillips 66 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 OVV 
 Ovintiv Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 XOM 
 Exxon Mobil Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 PXD 
 Pioneer Natural Resources Co 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 LNG 
 Cheniere Energy, Inc. 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 EMR 
 Emerson Electric Co. 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 UPS 
 United Parcel Service, Inc. 
 52 - Industrials 
 52405010 - Freight & Logistics - Courier, Postal, Air Freight & L

In [16]:
unique(arrange(rbind(mlvc2,mlsy),Ticker)) %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 ADP 
 Automatic Data Processing Inc 
 57 - Technology 
 57201010 - IT Services & Consulting 
 
 
 2 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 4 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 5 
 BNTX 
 BioNTech SE - ADR 
 56 - Healthcare 
 56202010 - Biotechnology & Medical Research 
 
 
 6 
 BP 
 BP plc (ADR) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 8 
 CEA 
 China Eastern Airlines Corp. L 
 52 - Industrials 
 52406010 - Airlines 
 
 
 9 
 CF 
 CF Industries Holdings, Inc. 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 11 
 CNC 
 Centene Corp 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 12 
 COP 
 ConocoPhillips 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 14 
 CVE 
 Cenovus Energy Inc (US) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 16 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 18 
 EMR 
 Emerson Electric Co. 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 20 
 ENB 
 Enbridge Inc (USA) 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 21 
 EQNR 
 Equinor ASA (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 23 
 ET 
 Energy Transfer LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 24 
 FIS 
 Fidelity National Information 
 57 - Technology 
 57301010 - Fintech 
 
 
 25 
 FISV 
 Fiserv Inc 
 52 - Industrials 
 52203040 - Business Support Services 
 
 
 26 
 GS 
 Goldman Sachs Group Inc 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 28 
 LNG 
 Cheniere Energy, Inc. 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 29 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 31 
 NTES 
 NetEase Inc (ADR) 
 57 - Technology 
 57201030 - Online Services 
 
 
 32 
 NXPI 
 NXP Semiconductors NV 
 57 - Technology 
 57101010 - Semiconductors 
 
 
 33 
 OVV 
 Ovintiv Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 35 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 37 
 PBR 
 Petroleo Brasileiro SA Petrobr 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 39 
 PPC 
 Pilgrim's Pride Corporation 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 40 
 PSX 
 Phillips 66 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 41 
 PXD 
 Pioneer Natural Resources Co 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 42 
 SHEL 
 Shell PLC (ADR) 
 50 - Energy 
 50102010 - Oil & Gas - Integrated 
 
 
 44 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 46 
 UPS 
 United Parcel Service, Inc. 
 52 - Industrials 
 52405010 - Freight & Logistics - Courier, Postal, Air Freight & L 
 
 
 48 
 WM 
 Waste Management, Inc. 
 52 - Industrials 
 52203010 - Environmental Services & Equipment 
 
 
 49 
 XOM 
 Exxon Mobil Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing

In [17]:
utilities <- allstocks %>%
  filter(Sector == "59  - Utilities") %>%
  arrange(desc(VC2)) %>%
  slice_head(n =25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
noncyc <- filter(allstocks,Sector == "54  - Consumer Non-Cyclicals") %>%
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
arrange(rbind(utilities,noncyc),Ticker)   %>%
  kable("html") %>%
  as.character() %>%
  display_html()

constap <- rbind(slice_head(noncyc,n=3),slice_head(utilities,n=3))

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 ABEV 
 Ambev SA (ADR) 
 54 - Consumer Non-Cyclicals 
 54101010 - Brewers 
 
 
 AGRO 
 Adecoagro SA 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 ALE 
 ALLETE Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 AVA 
 Avista Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 BTI 
 British American Tobacco PLC ( 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 CAH 
 Cardinal Health Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 CCU 
 Compania Cervecerias Unidas S. 
 54 - Consumer Non-Cyclicals 
 54101010 - Brewers 
 
 
 CIG 
 Energy of Minas Gerais Co 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 CSV 
 Carriage Services, Inc. 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 ENIC 
 Enel Chile SA - ADR 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 ETR 
 Entergy Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EVRG 
 Evergy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EXC 
 Exelon Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 FTS 
 Fortis Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HAIN 
 Hain Celestial Group Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HLF 
 Herbalife Nutrition Ltd 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HRB 
 H & R Block Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 KEN 
 Kenon Holdings Ltd 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 KEP 
 Korea Electric Power Corporati 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 KR 
 Kroger Co 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 MCK 
 McKesson Corporation 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 MDU 
 Mdu Resources Group Inc 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 MED 
 Medifast Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 MMM 
 3M Co 
 54 - Consumer Non-Cyclicals 
 54401010 - Consumer Goods Conglomerates 
 
 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OGE 
 OGE Energy Corp. 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OTTR 
 Otter Tail Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PAM 
 Pampa Energia S.A. (ADR) 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PCG 
 PG&E Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PM 
 Philip Morris International In 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 PNM 
 PNM Resources Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PNW 
 Pinnacle West Capital Corporat 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 POR 
 Portland General Electric Comp 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PPL 
 PPL Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 RLX 
 RLX Technology Inc - ADR 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 SBS 
 Companhia de Saneamento Bsc DE 
 59 - Utilities 
 59103010 - Utilities - Water & Related 
 
 
 SCI 
 Service Corporation Internatio 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SFM 
 Sprouts Farmers Market Inc 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 SR 
 Spire Inc 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 TAC 
 TransAlta Corporation (USA) 
 59 - Utilities 
 59101020 - Utilities - Independent Power Producers 
 
 
 TPB 
 Turning Point Brands Inc 
 54 - Consumer Non-Cyclicals 
 5